## 0. Cargar librería

In [1]:
import pandas as pd
import numpy as np
from sklearn.decomposition import TruncatedSVD
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
import matplotlib.pyplot as plt


# Mostrar todas las columnas en horizontal sin recortar
pd.set_option('display.max_columns', None)        # Mostrar todas las columnas
pd.set_option('display.max_colwidth', None)       # No cortar texto en columnas (como 'title')
pd.set_option('display.expand_frame_repr', False) # Mostrar DataFrame completo en una línea si cabe


## 1. Cargar datos 

In [2]:
# Cargar valoraciones generales
ratings = pd.read_csv("/kaggle/input/movielens/ratings.csv", 
                      dtype={'userId': 'int32', 'movieId': 'int32', 'rating': 'float32'})
ratings

userId  movieId  rating   timestamp
0            1        1     4.0   964982703
1            1        3     4.0   964981247
2            1        6     4.0   964982224
3            1       47     5.0   964983815
4            1       50     5.0   964982931
...        ...      ...     ...         ...
100831     610   166534     4.0  1493848402
100832     610   168248     5.0  1493850091
100833     610   168250     5.0  1494273047
100834     610   168252     5.0  1493846352
100835     610   170875     3.0  1493846415

[100836 rows x 4 columns]

In [3]:
# Cargar películas
movies = pd.read_csv("/kaggle/input/movielens/movies.csv", 
                     dtype={'movieId': 'int32', 'title': 'str'})
movies

movieId                                      title                                       genres
0           1                           Toy Story (1995)  Adventure|Animation|Children|Comedy|Fantasy
1           2                             Jumanji (1995)                   Adventure|Children|Fantasy
2           3                    Grumpier Old Men (1995)                               Comedy|Romance
3           4                   Waiting to Exhale (1995)                         Comedy|Drama|Romance
4           5         Father of the Bride Part II (1995)                                       Comedy
...       ...                                        ...                                          ...
9737   193581  Black Butler: Book of the Atlantic (2017)              Action|Animation|Comedy|Fantasy
9738   193583               No Game No Life: Zero (2017)                     Animation|Comedy|Fantasy
9739   193585                               Flint (2017)                                        Drama
9740   193587        Bungo Stray Dogs: Dead Apple (2018)                             Action|Animation
9741   193609        Andrew Dice Clay: Dice Rules (1991)                                       Comedy

[9742 rows x 3 columns]

In [4]:
# Cargar valoraciones del profesor
my_votem = pd.read_csv("/kaggle/input/movielens/myvotem.csv")

# Transformar formato para que encaje con ratings.csv
my_votem = my_votem.rename(columns={'score': 'rating'})
my_votem['userId'] = 1000  # asignamos el ID del profesor
my_votem

/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1458: RuntimeWarning: invalid value encountered in greater
  has_large_values = (abs_vals > 1e6).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in less
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in greater
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()


movieId  rating  userId
0     99999999     0.0    1000
1            3     1.0    1000
2            4     NaN    1000
3            5     2.0    1000
4            6     4.5    1000
...        ...     ...     ...
7500     88744     3.5    1000
7501     52281     4.0    1000
7502     57368     3.0    1000
7503      3424    -1.0    1000
7504     80549    -1.0    1000

[7505 rows x 3 columns]

In [5]:
# Unimos las valoraciones del profesor al conjunto de ratings
ratings = pd.concat([ratings, my_votem], ignore_index=True)
ratings

/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1458: RuntimeWarning: invalid value encountered in greater
  has_large_values = (abs_vals > 1e6).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in less
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in greater
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()


userId  movieId  rating    timestamp
0            1        1     4.0  964982703.0
1            1        3     4.0  964981247.0
2            1        6     4.0  964982224.0
3            1       47     5.0  964983815.0
4            1       50     5.0  964982931.0
...        ...      ...     ...          ...
108336    1000    88744     3.5          NaN
108337    1000    52281     4.0          NaN
108338    1000    57368     3.0          NaN
108339    1000     3424    -1.0          NaN
108340    1000    80549    -1.0          NaN

[108341 rows x 4 columns]

In [6]:
# Revisamos las valoraciones negativas del usuario profesor :(
print(ratings[ratings['userId'] == 1000].rating.describe())

count    6695.000000
mean       -0.233831
std         1.799715
min        -1.000000
25%        -1.000000
50%        -1.000000
75%        -1.000000
max         5.000000
Name: rating, dtype: float64


In [7]:
# Eliminamos las valoraciones negativas (-1.0)
ratings = ratings[ratings['rating'] >= 0]

# Verificamos que todo esté bien
print(ratings[ratings['userId'] == 1000].rating.describe())

count    1074.000000
mean        3.776071
std         1.018421
min         0.000000
25%         3.500000
50%         4.000000
75%         4.500000
max         5.000000
Name: rating, dtype: float64


/usr/local/lib/python3.10/dist-packages/pandas/core/computation/expressions.py:73: RuntimeWarning: invalid value encountered in greater_equal
  return op(a, b)


In [28]:
# Película favorita del profesor
my_vote = pd.read_csv("/kaggle/input/movielens/myvote.csv")
favorite_id = my_vote['movieId'].iloc[0]
favorite_title = movies[movies['movieId'] == favorite_id]['title'].values[0]
print(f"Película favorita del profesor: {favorite_title}")

movies[movies['movieId'] == 356]

Película favorita del profesor: Forrest Gump (1994)


movieId                title                    genres
314      356  Forrest Gump (1994)  Comedy|Drama|Romance|War

## 2. Crear matriz de utilidad y filtrado

In [9]:
# Matriz de utilidad: usuarios × películas
ratings_matrix = ratings.pivot_table(index='userId', columns='movieId', values='rating')

# Mostrar solo un fragmento de la matriz
ratings_matrix.head(10)

/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1458: RuntimeWarning: invalid value encountered in greater
  has_large_values = (abs_vals > 1e6).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in less
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in greater
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()


movieId  1         2         3         4         5         6         7         8         9         10        11        12        13        14        15        16        17        18        19        20        21        22        23        24        25        26        27        28        29        30        31        32        34        36        38        39        40        41        42        43        44        45        46        47        48        49        50        52        53        54        55        57        58        60        61        62        63        64        65        66        68        69        70        71        72        73        74        75        76        77        78        79        80        81        82        83        85        86        87        88        89        92        93        94        95        96        97        99        100       101       102       103       104       105       106       107       108       110       111       112       113       116       117       118       119       121       122       123       125       126       128       129       132       135       137       140       141       144       145       146       147       148       149       150       151       152       153       154       155       156       157       158       159       160       161       162       163       164       165       166       168       169       170       171       172       173       174       175       176       177       178       179       180       181       183       184       185       186       187       188       189       190       191       193       194       195       196       198       199       201       202       203       204       205       206       207       208       209       210       211       212       213       214       215       216       217       218       219       220       222       223       224       225       227       228       229       230       231       232       233       234       235       236       237       238       239       240       241       242       243       246       247       248       249       250       251       252       253       254       255       256       257       258       259       260       261       262       263       265       266       267       269       270       271       272       273       274       275       276       277       278       279       280       281       282       283       284       285       287       288       289       290       291       292       293       294       295       296       298       299       300       301       302       303       304       305       306       307       308       310       311       312       313       314       315       316       317       318       319       320       321       322       324       325       326       327       328       329       330       331       332       333       334       335       336       337       338       339       340       341       342       343       344       345       346       347       348       349       350       351       352       353       354       355       356       357       358       359       360       361       362       363       364       365       366       367       368       369       370       371       372       373       374       376       377       378       379       380       381       382       383       384       385       386       387       388       389       390       391       393       405       406       407       408       409       410       412       413       414       415       416       417       418       419       420       421       422       423       424       425       426       427       428       429       430       431       432       433       434       435       436       437       438       440       441       442       444       445       446       448       449       450       451       452       453       454       455       456       457       4

In [10]:
# Filtrar películas con al menos 10 valoraciones
valid_movies = ratings_matrix.count(axis=0) > 10
ratings_matrix = ratings_matrix.loc[:, valid_movies]

# Filtrar usuarios con al menos 30 valoraciones
valid_users = ratings_matrix.count(axis=1) > 30
ratings_matrix = ratings_matrix.loc[valid_users, :]
ratings_matrix

/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1458: RuntimeWarning: invalid value encountered in greater
  has_large_values = (abs_vals > 1e6).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in less
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in greater
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()


movieId  1       2       3       5       6       7       9       10      11      12      14      15      16      17      18      19      20      21      22      23      24      25      26      28      29      31      32      34      36      39      41      44      45      46      47      48      50      52      58      60      62      65      69      70      73      76      79      81      86      88      95      100     101     104     105     107     110     111     112     122     125     135     140     141     144     145     147     150     151     153     154     157     158     159     160     161     162     163     164     165     168     169     170     172     173     175     176     180     181     185     186     188     193     194     196     198     203     204     207     208     215     216     218     222     223     224     225     227     230     231     232     233     234     235     236     237     239     246     247     248     249     252     253     256     257     260     261     262     265     266     267     272     273     276     277     280     281     282     288     290     292     293     296     300     303     306     307     308     314     315     316     317     318     319     327     329     332     333     337     338     339     342     344     345     348     349     350     351     353     355     356     357     361     362     364     366     367     368     370     371     372     373     374     376     377     379     380     381     382     383     393     405     410     412     413     415     417     419     420     421     427     428     431     432     434     435     440     441     442     445     454     455     457     466     468     471     474     475     477     480     481     485     489     490     491     492     493     494     497     500     502     507     508     509     514     515     516     519     520     524     527     529     531     532     533     534     535     537     538     539     540     541     542     543     546     551     552     553     555     562     575     585     586     587     588     589     590     592     593     594     595     596     597     599     608     609     610     616     628     631     637     640     647     648     653     661     663     671     673     694     707     708     709     714     719     720     724     733     736     737     741     742     743     745     748     750     761     762     765     778     780     783     784     785     786     788     798     799     800     801     802     805     810     830     832     836     837     838     839     842     849     852     858     866     880     892     898     899     900     902     903     904     905     908     909     910     911     912     913     914     915     916     919     920     922     923     924     926     928     930     933     934     951     952     953     954     955     965     968     969     986     991     994     996     999     1013    1015    1019    1020    1021    1022    1023    1025    1027    1028    1029    1030    1031    1032    1033    1035    1036    1037    1041    1042    1047    1049    1057    1059    1060    1061    1064    1073    1077    1078    1079    1080    1081    1084    1086    1088    1089    1090    1091    1092    1093    1094    1095    1097    1100    1101    1103    1104    1120    1124    1125    1127    1129    1131    1135    1136    1148    1171    1172    1173    1175    1178    1179    1183    1186    1188    1189    1193    1194    1196    1197    1198    1199    1200    1201    1203    1204    1206    1207    1208    1209    1210    1211    1212    1213    1214    1215    1216    1217    1218    1219    1220    1221    1222    1223    1224    1225    1227    1228    1230    1231    1233    1234    1235    1237    1240    1242    1243    1244    1245    1246    1247    1248    1249    1250    1251    1252    1253    1254    1256    1257    1258    1259    1260   

## 3. Recomendación colaborativa con SVD

In [11]:
def predict_svd(ratings_matrix, n_components=50):
    # Calcula la media de cada usuario
    user_means = ratings_matrix.mean(axis=1)

    # Centra las valoraciones: resta la media de cada usuario
    centered = ratings_matrix.sub(user_means, axis=0)

    # Rellena los valores NA con ceros (para aplicar SVD)
    filled = centered.fillna(0)

    # Aplica SVD
    svd = TruncatedSVD(n_components=n_components, random_state=42)
    M = svd.fit_transform(filled)  # Matriz de usuarios en espacio reducido
    Sigma = np.diag(svd.singular_values_)  # Valores singulares
    V = svd.components_  # Componentes latentes de las películas

    # Reconstruye la matriz de predicciones
    estimated = np.dot(np.dot(M, Sigma), V)

    # Convierte a DataFrame con los mismos índices y columnas
    predictions = pd.DataFrame(estimated, index=ratings_matrix.index, columns=ratings_matrix.columns)

    # Vuelve a sumar las medias del usuario para descentrar
    predictions = predictions.add(user_means, axis=0)

    return predictions


# Generar matriz de predicciones con SVD
predicted_matrix = predict_svd(ratings_matrix, n_components=50)
predicted_matrix

movieId     1          2          3          5          6          7          9          10         11         12        14        15         16         17        18         19         20         21        22         23         24        25        26        28         29         31         32         34        36         39        41         44        45        46         47         48         50        52        58         60         62         65        69         70        73        76        79        81        86         88         95        100        101        104        105       107        110        111       112        122        125       135       140       141       144        145       147        150        151         153       154       157        158       159        160        161        162        163       164        165        168        169        170        172        173        175        176        180        181        185        186        188        193        194        196       198        203        204       207        208        215        216       218        222        223        224       225       227       230        231        232       233       234        235       236       237       239        246        247       248       249        252        253        256       257         260        261       262        265        266        267       272       273       276        277       280       281        282        288       290        292        293         296        300        303        306        307        308       314        315        316        317         318        319       327       329        332        333        337       338        339        342        344        345        348        349        350       351        353         355        356        357       361       362        364        366        367       368        370       371       372       373        374       376        377        379        380       381        382        383        393        405        410        412        413        415        417        419         420       421       427        428        431        432        434         435       440        441        442        445        454        455        457        466       468        471        474        475       477        480       481        485       489       490       491        492       493       494        497        500        502       507        508        509        514       515       516        519        520       524        527       529        531       532       533       534       535       537        538        539       540        541       542       543         546        551        552        553        555       562        575        585        586        587        588        589        590        592        593        594        595        596        597        599        608       609        610        616       628       631       637       640       647        648        653       661       663        671         673       694       707        708       709        714        719        720       724        733        736        737        741       742        743        745       748        750       761        762       765        778        780        783        784        785        786        788        798        799       800       801        802       805        810       830       832        836       837       838        839        842        849        852         858        866        880       892        898        899       900        902        903        904        905        908        909        910        911        912        913        914        915        916        919        920        922        923        924        926        928        930        933       934        951       952        953        954        955       965        968        969       986       991        994   

## 4. Recomendaciones para el profesor (usuario 1000)

In [12]:
# Seleccionar el usuario del profesor
userId = 1000

# Extraer predicciones de puntuación para el profesor
predictions = predicted_matrix.loc[userId]
predictions

movieId
1         46.726718
2         -0.409094
3        -82.834868
5        -68.125165
6         44.648848
            ...    
174055    12.325570
176371    31.841094
177765     3.065124
179819   -13.102715
187593    31.870479
Name: 1000, Length: 2146, dtype: float64

In [13]:
# Películas ya vistas por el profesor
already_rated = ratings_matrix.loc[userId].dropna().index
already_rated

# Filtrar solo las no vistas y seleccionar las mejores
recommendations = predictions.drop(index=already_rated)
top_recs = recommendations.sort_values(ascending=False).head(10)
top_recs

movieId
1080     34.950501
2502     34.097189
3275     31.119803
5618     30.286228
78499    28.155859
904      27.129985
38061    27.035672
57669    26.597238
2918     26.366346
1967     26.032800
Name: 1000, dtype: float64

In [14]:
# Añadir los títulos de las películas recomendadas
final_recs = pd.merge(top_recs.to_frame(name='predicted_rating'), 
                      movies, left_index=True, right_on='movieId')

final_recs = final_recs[['movieId', 'title', 'predicted_rating']].sort_values(by='predicted_rating', ascending=False)

# Mostrar recomendaciones finales
print("Recomendaciones colaborativas para el profesor (ordenadas):")
print(final_recs)

Recomendaciones colaborativas para el profesor (ordenadas):
      movieId                                                 title  predicted_rating
820      1080                   Monty Python's Life of Brian (1979)         34.950501
1883     2502                                   Office Space (1999)         34.097189
2462     3275                           Boondock Saints, The (2000)         31.119803
3984     5618  Spirited Away (Sen to Chihiro no kamikakushi) (2001)         30.286228
7355    78499                                    Toy Story 3 (2010)         28.155859
686       904                                    Rear Window (1954)         27.129985
6016    38061                            Kiss Kiss Bang Bang (2005)         27.035672
6676    57669                                      In Bruges (2008)         26.597238
2195     2918                       Ferris Bueller's Day Off (1986)         26.366346
1444     1967                                      Labyrinth (1986)         26.0

## 5. Evaluación con matriz de confusión 


In [15]:
# Crear matriz de confusión vacía
conf_matrix = np.zeros((2, 2), dtype=int)

# Películas valoradas por el profesor
viewed = ratings_matrix.loc[userId].dropna()
print(f"\n Películas valoradas por el profesor:{viewed.count()}")
display(viewed.head(10))  # muestra las primeras 10

# Películas que el profesor considera buenas (rating > 3.5)
good = viewed[viewed > 3.5]
print(f"\n Películas consideradas 'buenas': {good.count()}")
display(good.head(10))

# Número de recomendaciones a comparar (top-N)
top_n = good.count()
print(f"\n Número de recomendaciones a comparar (top_n): {top_n}")


 Películas valoradas por el profesor:817


movieId
1     4.5
2     4.0
3     1.0
5     2.0
6     4.5
7     2.0
9     2.5
10    4.0
11    4.0
12    4.5
Name: 1000, dtype: float64


 Películas consideradas 'buenas': 524


movieId
1     4.5
2     4.0
6     4.5
10    4.0
11    4.0
12    4.5
15    4.0
16    4.0
19    4.5
29    5.0
Name: 1000, dtype: float64


 Número de recomendaciones a comparar (top_n): 524


In [16]:
# Simulación: 524 películas buenas valoradas por el profesor
for movie_id in viewed.index[:524]:  # Limitamos por velocidad
    # Simulamos que el profesor no ha visto esta película
    temp_matrix = ratings_matrix.copy()
    temp_matrix.at[userId, movie_id] = np.nan

    # Recalculamos predicciones sin esa película
    preds = predict_svd(temp_matrix, n_components=50)
    top_preds = preds.loc[userId].sort_values(ascending=False).iloc[:top_n]

    # Evaluamos si la película "buena" fue recomendada
    if movie_id in good.index and movie_id in top_preds.index:
        conf_matrix[0][0] += 1  # True Positive
    elif movie_id not in good.index and movie_id in top_preds.index:
        conf_matrix[0][1] += 1  # False Positive
    elif movie_id in good.index and movie_id not in top_preds.index:
        conf_matrix[1][0] += 1  # False Negative
    else:
        conf_matrix[1][1] += 1  # True Negative

# Mostrar matriz de confusión final
print("Matriz de confusión:\n", conf_matrix)

Matriz de confusión:
 [[156  16]
 [180 172]]


In [17]:
# Extraer valores
TP, FP, FN, TN = conf_matrix[0][0], conf_matrix[0][1], conf_matrix[1][0], conf_matrix[1][1]

# Métricas de evaluación
precision = TP / (TP + FP) if (TP + FP) > 0 else 0
recall    = TP / (TP + FN) if (TP + FN) > 0 else 0
f1        = 2 * precision * recall / (precision + recall) if (precision + recall) > 0 else 0

# Mostrar métricas
print(f"Precisión: {precision:.2f}")
print(f"Recall: {recall:.2f}")
print(f"F1 Score: {f1:.2f}")


Precisión: 0.91
Recall: 0.46
F1 Score: 0.61


## Metodo alternativo: Compara sin eliminar peliculas, revisando si las peliculas qeu le gusta el profesor estan entre las qeu el sistema recomienda por defecto

In [18]:
# Resultado por top-N
resultados = []

# Lista de valores de top_n que quieres probar
top_n_values = [10, 20, 50, 100, 200, 524]  # 524 es el total de buenas

# Películas buenas
userId = 1000
viewed = ratings_matrix.loc[userId].dropna()
good = viewed[viewed > 3.5]

# Calcular predicciones una sola vez
predicted_matrix = predict_svd(ratings_matrix, n_components=50)
predictions = predicted_matrix.loc[userId].sort_values(ascending=False)

for top_n in top_n_values:
    top_preds = predictions.iloc[:top_n].index

    conf_matrix = np.zeros((2, 2), dtype=int)

    for movie_id in viewed.index:
        if movie_id in good.index and movie_id in top_preds:
            conf_matrix[0][0] += 1  # TP
        elif movie_id not in good.index and movie_id in top_preds:
            conf_matrix[0][1] += 1  # FP
        elif movie_id in good.index and movie_id not in top_preds:
            conf_matrix[1][0] += 1  # FN
        else:
            conf_matrix[1][1] += 1  # TN

    TP, FP, FN, TN = conf_matrix[0][0], conf_matrix[0][1], conf_matrix[1][0], conf_matrix[1][1]
    precision = TP / (TP + FP) if (TP + FP) > 0 else 0
    recall    = TP / (TP + FN) if (TP + FN) > 0 else 0
    f1        = 2 * precision * recall / (precision + recall) if (precision + recall) > 0 else 0

    resultados.append({
        'top_n': top_n,
        'TP': TP, 'FP': FP, 'FN': FN, 'TN': TN,
        'Precision': round(precision, 3),
        'Recall': round(recall, 3),
        'F1': round(f1, 3)
    })

# Convertimos a DataFrame para ver todo junto
df_resultados = pd.DataFrame(resultados)
display(df_resultados)

top_n   TP  FP   FN   TN  Precision  Recall     F1
0     10   10   0  514  293      1.000   0.019  0.037
1     20   20   0  504  293      1.000   0.038  0.074
2     50   50   0  474  293      1.000   0.095  0.174
3    100  100   0  424  293      1.000   0.191  0.321
4    200  198   0  326  293      1.000   0.378  0.548
5    524  378   6  146  287      0.984   0.721  0.833

## Peliculas buenas según el sistema que no ha visto el profesor

In [26]:
# Repetimos el preprocesado base por claridad
userId = 1000
predictions = predicted_matrix.loc[userId].sort_values(ascending=False)
real_ratings = ratings_matrix.loc[userId]

# Crear dataframe con predicciones
df_recs = predictions.to_frame(name='predicted_rating')
df_recs.index.name = 'movieId'
df_recs.reset_index(inplace=True)

# Añadir títulos y valoraciones reales
df_recs = pd.merge(df_recs, movies, on='movieId', how='left')
df_recs['rating_profesor'] = df_recs['movieId'].map(real_ratings)
df_recs['vista_por_profesor'] = df_recs['rating_profesor'].notna()

# Ordenar por recomendación
df_recs = df_recs.sort_values(by='predicted_rating', ascending=False)


In [27]:
# Definimos una "alta recomendación" como estar en el top 20% de predicción
umbral_recomendacion = df_recs['predicted_rating'].quantile(0.80)

df_nuevas_para_profesor = df_recs[
    (df_recs['vista_por_profesor'] == False) &
    (df_recs['predicted_rating'] >= umbral_recomendacion)
]

display(df_nuevas_para_profesor.head(10))


/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1458: RuntimeWarning: invalid value encountered in greater
  has_large_values = (abs_vals > 1e6).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in less
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()
/usr/local/lib/python3.10/dist-packages/pandas/io/formats/format.py:1459: RuntimeWarning: invalid value encountered in greater
  has_small_values = ((abs_vals < 10 ** (-self.digits)) & (abs_vals > 0)).any()


movieId  predicted_rating                                                 title                                            genres  rating_profesor  vista_por_profesor
185     1080         34.950501                   Monty Python's Life of Brian (1979)                                            Comedy              NaN               False
190     2502         34.097189                                   Office Space (1999)                                      Comedy|Crime              NaN               False
216     3275         31.119803                           Boondock Saints, The (2000)                       Action|Crime|Drama|Thriller              NaN               False
220     5618         30.286228  Spirited Away (Sen to Chihiro no kamikakushi) (2001)                       Adventure|Animation|Fantasy              NaN               False
236    78499         28.155859                                    Toy Story 3 (2010)  Adventure|Animation|Children|Comedy|Fantasy|IMAX              NaN               False
245      904         27.129985                                    Rear Window (1954)                                  Mystery|Thriller              NaN               False
247    38061         27.035672                            Kiss Kiss Bang Bang (2005)                     Comedy|Crime|Mystery|Thriller              NaN               False
249    57669         26.597238                                      In Bruges (2008)                       Comedy|Crime|Drama|Thriller              NaN               False
253     2918         26.366346                       Ferris Bueller's Day Off (1986)                                            Comedy              NaN               False
259     1967         26.032800                                      Labyrinth (1986)                         Adventure|Fantasy|Musical              NaN               False

## 6. Recomendación basada en contenido (TF-IDF)

In [23]:
# Limpieza de géneros
movies['genres'] = movies['genres'].fillna('')

# Vectorización TF-IDF
tfidf = TfidfVectorizer(stop_words='english')
tfidf_matrix = tfidf.fit_transform(movies['genres'])

# Similitud del coseno
cosine_sim = linear_kernel(tfidf_matrix, tfidf_matrix)
indices = pd.Series(movies.index, index=movies['movieId'])

# Recomendaciones similares a la favorita del profesor
idx = indices[favorite_id]
sim_scores = list(enumerate(cosine_sim[idx]))
sim_scores = sorted(sim_scores, key=lambda x: x[1], reverse=True)
sim_scores = sim_scores[1:11]
movie_indices = [i[0] for i in sim_scores]

content_recs = movies.iloc[movie_indices][['title']]
print("\n Recomendaciones por contenido (basadas en su favorita):")
print(content_recs)


 Recomendaciones por contenido (basadas en su favorita):
                                                                       title
1730                              Life Is Beautiful (La Vita è bella) (1997)
2262                                     Train of Life (Train de vie) (1998)
6296                     Tiger and the Snow, The (La tigre e la neve) (2005)
6624  I Served the King of England (Obsluhoval jsem anglického krále) (2006)
346                                               Colonel Chabert, Le (1994)
702                                                Gone with the Wind (1939)
886                                              English Patient, The (1996)
1421                                            From Here to Eternity (1953)
1532                                                   Doctor Zhivago (1965)
2051                                                     Barry Lyndon (1975)


In [24]:
# 1. Índice de la película favorita
idx = indices[favorite_id]

# 2. Calcular similitud con todas las películas
sim_scores = list(enumerate(cosine_sim[idx]))
sim_scores = sorted(sim_scores, key=lambda x: x[1], reverse=True)

# 3. Convertimos a dataframe
sim_df = pd.DataFrame(sim_scores, columns=['idx', 'similaridad'])
sim_df['movieId'] = movies.iloc[sim_df['idx']].movieId.values

# 4. Unimos con títulos y géneros
content_recs = pd.merge(sim_df, movies[['movieId', 'title', 'genres']], on='movieId', how='left')

# 5. Añadimos la valoración del profesor (NaN = no vista)
content_recs['rating_profesor'] = content_recs['movieId'].map(ratings_matrix.loc[1000])

# 6. Filtramos solo películas NO vistas
content_recs_no_vistas = content_recs[content_recs['rating_profesor'].isna()]

# 7. Nos quedamos con las top 10 similares no vistas
content_recs_no_vistas = content_recs_no_vistas.sort_values(by='similaridad', ascending=False).head(10)

# 8. Seleccionar columnas finales ordenadas
content_recs_no_vistas = content_recs_no_vistas[['movieId', 'title', 'genres', 'similaridad']]

# Mostrar resultado
print("Recomendaciones por contenido (no vistas por el profesor):")
display(content_recs_no_vistas)


Recomendaciones por contenido (no vistas por el profesor):


movieId                                                                   title                    genres  similaridad
1      2324                              Life Is Beautiful (La Vita è bella) (1997)  Comedy|Drama|Romance|War     1.000000
3     48032                     Tiger and the Snow, The (La tigre e la neve) (2005)  Comedy|Drama|Romance|War     1.000000
4     56060  I Served the King of England (Obsluhoval jsem anglického krále) (2006)  Comedy|Drama|Romance|War     1.000000
2      3003                                     Train of Life (Train de vie) (1998)  Comedy|Drama|Romance|War     1.000000
17     4727                                       Captain Corelli's Mandolin (2001)         Drama|Romance|War     0.940253
28   140627                                            Battle For Sevastopol (2015)         Drama|Romance|War     0.940253
27    74688                                                        Dear John (2010)         Drama|Romance|War     0.940253
26    72479                                                   Messenger, The (2009)         Drama|Romance|War     0.940253
25    60894                                                Edge of Love, The (2008)         Drama|Romance|War     0.940253
24    55052                                                        Atonement (2007)         Drama|Romance|War     0.940253

# RECOMENDACIÓN FINAL

In [27]:
# Fusionar recomendaciones del sistema colaborativo y de contenido
recs_hibridas = pd.merge(
    df_nuevas_para_profesor,
    content_recs_no_vistas,
    on='movieId',
    how='inner'
)

# Seleccionar columnas relevantes (ajustadas según los nombres actuales)
recs_hibridas = recs_hibridas[['movieId', 'title_x', 'genres_y', 'predicted_rating', 'similaridad']]

# Renombrar columnas para dejarlo limpio
recs_hibridas = recs_hibridas.rename(columns={
    'title_x': 'title',
    'genres_y': 'genres'
})

# Calcular puntuación media entre ambos sistemas
recs_hibridas['score_medio'] = (recs_hibridas['predicted_rating'] + recs_hibridas['similaridad']) / 2

# Ordenar por score medio
recs_hibridas = recs_hibridas.sort_values(by='score_medio', ascending=False)

# Mostrar top 10 recomendaciones híbridas
print("Recomendaciones híbridas (colaborativo + contenido):")
display(recs_hibridas.head(10))




Recomendaciones híbridas (colaborativo + contenido):


movieId                                       title                    genres  predicted_rating  similaridad  score_medio
0     2324  Life Is Beautiful (La Vita è bella) (1997)  Comedy|Drama|Romance|War         24.705985          1.0    12.852992